# Segmenting and Clustering Neighborhoods in Toronto

## Part 1

Let's start by importing everything we will need

In [44]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt 

We can use the read_html function from pandas to obtain the content of the wiki site.

In [3]:
wiki = pd.read_html('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M', header=0)
wiki

[    Postal Code           Borough  \
 0           M1A      Not assigned   
 1           M2A      Not assigned   
 2           M3A        North York   
 3           M4A        North York   
 4           M5A  Downtown Toronto   
 ..          ...               ...   
 175         M5Z      Not assigned   
 176         M6Z      Not assigned   
 177         M7Z      Not assigned   
 178         M8Z         Etobicoke   
 179         M9Z      Not assigned   
 
                                          Neighbourhood  
 0                                         Not assigned  
 1                                         Not assigned  
 2                                            Parkwoods  
 3                                     Victoria Village  
 4                            Regent Park, Harbourfront  
 ..                                                 ...  
 175                                       Not assigned  
 176                                       Not assigned  
 177                

This returns a list of multple tables scraped from the wiki. We are only interessted in the first table

In [4]:
df=wiki[0]
df

Postal Code           Borough  \
0           M1A      Not assigned   
1           M2A      Not assigned   
2           M3A        North York   
3           M4A        North York   
4           M5A  Downtown Toronto   
..          ...               ...   
175         M5Z      Not assigned   
176         M6Z      Not assigned   
177         M7Z      Not assigned   
178         M8Z         Etobicoke   
179         M9Z      Not assigned   

                                         Neighbourhood  
0                                         Not assigned  
1                                         Not assigned  
2                                            Parkwoods  
3                                     Victoria Village  
4                            Regent Park, Harbourfront  
..                                                 ...  
175                                       Not assigned  
176                                       Not assigned  
177                                       Not assigned  
178  Mimico NW, The Queensway West, South of Bloor,...  
179                                       Not assigned  

[180 rows x 3 columns]

Let's drop all rows with "Not assigned" Borough. We do this by checking if the Borough Field contains "Not assigned", finding the inverse of the resulting boolean array with "~" and applying the resulting mask to our original dataframe.

In [5]:
df=df[~df['Borough'].str.contains('Not assigned')]
df.head(11)

Postal Code           Borough                                Neighbourhood
2          M3A        North York                                    Parkwoods
3          M4A        North York                             Victoria Village
4          M5A  Downtown Toronto                    Regent Park, Harbourfront
5          M6A        North York             Lawrence Manor, Lawrence Heights
6          M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government
8          M9A         Etobicoke      Islington Avenue, Humber Valley Village
9          M1B       Scarborough                               Malvern, Rouge
11         M3B        North York                                    Don Mills
12         M4B         East York              Parkview Hill, Woodbine Gardens
13         M5B  Downtown Toronto                     Garden District, Ryerson
14         M6B        North York                                    Glencairn

Let's check if we have any 'Not assigned' values in the Neighbourhood column.

In [6]:
df[df['Neighbourhood'].str.contains('Not assigned')]

Empty DataFrame
Columns: [Postal Code, Borough, Neighbourhood]
Index: []

This looks good! Now we use the shape method.

In [7]:
df.shape

(103, 3)

## End of Part 1 Beginning of Part 2

In [8]:
!pip install geocoder
import geocoder

The geocoder does not work for me so I will use the csv.

In [9]:
!wget -O coordinates.csv http://cocl.us/Geospatial_data
df_coord = pd.read_csv('coordinates.csv')
df_coord

--2020-08-08 09:50:01--  http://cocl.us/Geospatial_data
Resolving cocl.us (cocl.us)... 169.55.161.7
Connecting to cocl.us (cocl.us)|169.55.161.7|:80... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: https://cocl.us/Geospatial_data [following]
--2020-08-08 09:50:02--  https://cocl.us/Geospatial_data
Connecting to cocl.us (cocl.us)|169.55.161.7|:443... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: https://ibm.box.com/shared/static/9afzr83pps4pwf2smjjcf1y5mvgb18rr.csv [following]
--2020-08-08 09:50:03--  https://ibm.box.com/shared/static/9afzr83pps4pwf2smjjcf1y5mvgb18rr.csv
Resolving ibm.box.com (ibm.box.com)... 185.235.236.197
Connecting to ibm.box.com (ibm.box.com)|185.235.236.197|:443... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: /public/static/9afzr83pps4pwf2smjjcf1y5mvgb18rr.csv [following]
--2020-08-08 09:50:03--  https://ibm.box.com/public/static/9afzr83pps4pwf2smjjcf1y5

Postal Code   Latitude  Longitude
0           M1B  43.806686 -79.194353
1           M1C  43.784535 -79.160497
2           M1E  43.763573 -79.188711
3           M1G  43.770992 -79.216917
4           M1H  43.773136 -79.239476
..          ...        ...        ...
98          M9N  43.706876 -79.518188
99          M9P  43.696319 -79.532242
100         M9R  43.688905 -79.554724
101         M9V  43.739416 -79.588437
102         M9W  43.706748 -79.594054

[103 rows x 3 columns]

Now we need to merge the two dataframes. We use the merge functions so we can join on the Postal code column of the data frames

In [10]:
df2=pd.merge(df,df_coord, on='Postal Code')
df2

Postal Code           Borough  \
0           M3A        North York   
1           M4A        North York   
2           M5A  Downtown Toronto   
3           M6A        North York   
4           M7A  Downtown Toronto   
..          ...               ...   
98          M8X         Etobicoke   
99          M4Y  Downtown Toronto   
100         M7Y      East Toronto   
101         M8Y         Etobicoke   
102         M8Z         Etobicoke   

                                         Neighbourhood   Latitude  Longitude  
0                                            Parkwoods  43.753259 -79.329656  
1                                     Victoria Village  43.725882 -79.315572  
2                            Regent Park, Harbourfront  43.654260 -79.360636  
3                     Lawrence Manor, Lawrence Heights  43.718518 -79.464763  
4          Queen's Park, Ontario Provincial Government  43.662301 -79.389494  
..                                                 ...        ...        ...  
98       The Kingsway, Montgomery Road, Old Mill North  43.653654 -79.506944  
99                                Church and Wellesley  43.665860 -79.383160  
100  Business reply mail Processing Centre, South C...  43.662744 -79.321558  
101  Old Mill South, King's Mill Park, Sunnylea, Hu...  43.636258 -79.498509  
102  Mimico NW, The Queensway West, South of Bloor,...  43.628841 -79.520999  

[103 rows x 5 columns]

## End of Part 2, Beginning of Part 3

Let's have a look at the neighbourhoods on a map. First we install and import folium. We additionally need requests

In [11]:
!pip install folium
import folium
import requests

Second, we plot the neighbourhoods on the map and give the different boroughs different colors.

In [52]:
#longitude and latitude of toronto
lat=43.66135
long=-79.383087

map_toronto = folium.Map(location=[lat, long], zoom_start=10,control_scale = True)

#array with multiple colors
palette = ['blue', 'cadetblue', 'darkblue', 'darkgreen', 'darkpurple', 'darkred', 'gray', 'green', 'lightblue', 'lightgray', 'lightgreen', 'lightred', 'orange', 'pink', 'purple', 'red', 'white','beige','black']

for i,bor in enumerate(pd.unique(df['Borough'])):
    df3=df2[df2['Borough'].str.match(bor)]
    for lat, lng, neigh in zip(df3['Latitude'], df3['Longitude'], df3['Neighbourhood']):
        label = folium.Popup(neigh, parse_html=True)
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup="<b>"+ bor + "</b>: " + neigh,
            color=palette[i],
            fill=True,
            fill_color=palette[i],
            fill_opacity=1,
            parse_html=False).add_to(map_toronto)

map_toronto

We would like to get the venues of every Neighbourhood. We do this in 4 steps, later we will put the last 3 steps in a loop.

**First step:**
Set the basic parameters for Foursquare:

I use the getpass library to keep my credentials secret.

In [108]:
import getpass
CLIENT_ID = getpass.getpass('ID:')
CLIENT_SECRET = getpass.getpass('SECRET:')
VERSION = '20180605' # Foursquare API version

ID:········
SECRET:········


**Second step:**
get all venues of a neighbourhood, in this example it is the neighbourhood with the index 3, which is Lawrence Manor, Lawrence Heights. Foursquare returns a maximum of 100 venues. Since the neighbourhoods in the city centre are closer together than the neighbourhoods in the suburbs we need an adaptive approach to get as many venues as possible. If our requeste returns a number of venues that is below 50 we will increase the radius and repeat the request. We start at a radius of 800. 

In [109]:
j=3
neighborhood_latitude = df2.loc[j, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = df2.loc[j, 'Longitude'] # neighborhood longitude value
name=df2.loc[j, 'Neighbourhood']
radius=800
LIMIT=100
nvenues=0
while nvenues<50:
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{}&v={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, neighborhood_latitude, neighborhood_longitude, VERSION, radius, LIMIT)
    results = requests.get(url).json()
    nvenues=len(results['response']['groups'][0]['items'])
    if (nvenues <50):
        radius=radius+300
        print(name+ ': '+str(nvenues) + ' venues found, radius increased to '+str(radius))
    else:
        print(name+ ': '+str(nvenues) + ' venues found')
        
items = results['response']['groups'][0]['items']
items

Lawrence Manor, Lawrence Heights: 35 venues found, radius increased to 1100
Lawrence Manor, Lawrence Heights: 55 venues found


[{'reasons': {'count': 0,
   'items': [{'summary': 'This spot is popular',
     'type': 'general',
     'reasonName': 'globalInteractionReason'}]},
  'venue': {'id': '4b16e8b6f964a52051bf23e3',
   'name': 'Roots',
   'location': {'address': '71-95 Orfus Road',
    'lat': 43.71821373389962,
    'lng': -79.46389305304558,
    'labeledLatLngs': [{'label': 'display',
      'lat': 43.71821373389962,
      'lng': -79.46389305304558}],
    'distance': 77,
    'postalCode': 'M6A 1L9',
    'cc': 'CA',
    'city': 'Toronto',
    'state': 'ON',
    'country': 'Canada',
    'formattedAddress': ['71-95 Orfus Road', 'Toronto ON M6A 1L9', 'Canada']},
   'categories': [{'id': '4bf58dd8d48988d104951735',
     'name': 'Boutique',
     'pluralName': 'Boutiques',
     'shortName': 'Boutique',
     'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/apparel_boutique_',
      'suffix': '.png'},
     'primary': True}],
   'photos': {'count': 0, 'groups': []}},
  'referralId': 'e-0-4b16e8b6f964a5

**Third step:** we convert the json file to a pd dataframe. In preparation of the next step we also convert the venue.location.formattedAddress field from an array to a string.

In [16]:
df_venue= pd.json_normalize(items)
df_venue['venue.location.formattedAddress']=df_venue['venue.location.formattedAddress'].apply(', '.join)
df_venue

referralId  reasons.count  \
0    e-0-4b16e8b6f964a52051bf23e3-0              0   
1    e-0-4ccc5aebee23a14370591ea8-1              0   
2    e-0-4b12e300f964a520299023e3-2              0   
3    e-0-54c3d9ed498e50c810920ee4-3              0   
4    e-0-4b5f1f11f964a52047a729e3-4              0   
5    e-0-55fc4738498ea821b8d881ae-5              0   
6    e-0-52ae475e498e1d931502955d-6              0   
7    e-0-5ae3d754d3cce8002c86cbe1-7              0   
8    e-0-4b0ecb01f964a5201b5b23e3-8              0   
9    e-0-4b9580fef964a52044a634e3-9              0   
10  e-0-4db7044fa86e8d2707b7795e-10              0   
11  e-0-4b0dacf6f964a520b54d23e3-11              0   
12  e-0-558371db498eb7238b3505eb-12              0   
13  e-0-4b9e6ed5f964a52048e336e3-13              0   
14  e-0-4b3a4021f964a520f76225e3-14              0   
15  e-0-507d95038055b398c78eec04-15              0   
16  e-0-4da88e6d5da3ef8bf1613837-16              0   
17  e-0-5a32e7f3f427de60fcef7751-17              0   
18  e-0-4fb903b8be774df11d9cacbc-18              0   
19  e-0-4b6f005af964a520f1d52ce3-19              0   
20  e-0-4af79aadf964a520070a22e3-20              0   
21  e-0-5c426e34065ef5002c050b40-21              0   
22  e-0-4bf71abfb182c9b66829755a-22              0   
23  e-0-4bf5b47594b2a593c623acee-23              0   
24  e-0-4be8263a947820a1a283b4db-24              0   
25  e-0-4fa4ae40e4b02443361f27c4-25              0   
26  e-0-4be35c5eb02ec9b64c644fc0-26              0   
27  e-0-4e418f4f1f6e4d7545b7c976-27              0   
28  e-0-4b6efb06f964a52085d42ce3-28              0   
29  e-0-4fd29768e4b008dc358830f5-29              0   
30  e-0-5218128011d2f9bf38d27de8-30              0   
31  e-0-4becbb0b0ddaa593c5041ec3-31              0   
32  e-0-4c581533d12a20a1941768bd-32              0   
33  e-0-4ca0f97c8afca09344681716-33              0   
34  e-0-4fca5aeee4b053b8ae5eba6d-34              0   
35  e-0-4ae8b081f964a5207cb121e3-35              0   
36  e-0-4baf6adff964a52035fe3be3-36              0   
37  e-0-4b1575d6f964a52028ad23e3-37              0   
38  e-0-4b06df4af964a520ebf122e3-38              0   
39  e-0-4d4c0bde5f9db60c324a3150-39              0   
40  e-0-4e24384e22717a5245e621a4-40              0   
41  e-0-4af3820ef964a5203dee21e3-41              0   
42  e-0-4b008142f964a520fc3e22e3-42              0   
43  e-0-4b896e06f964a520803532e3-43              0   
44  e-0-4bb4d8736444b7130fbbf300-44              0   
45  e-0-4ae766baf964a520fcaa21e3-45              0   
46  e-0-4c20f62eebe52d7f1f6f3178-46              0   
47  e-0-4c228e6e13c00f4715b287de-47              0   
48  e-0-4b8951ebf964a520522b32e3-48              0   
49  e-0-4c2a45962219c928ecd5a248-49              0   
50  e-0-530e5a4e498e9d17ab15ae5d-50              0   
51  e-0-4bb0e834f964a520e6683ce3-51              0   
52  e-0-59e7ba996bdee6069e7c2ee9-52              0   
53  e-0-4e0f938d7d8bb178a8b434f8-53              0   
54  e-0-4c42343ed691c9b6c3018e0a-54              0   

                                        reasons.items  \
0   [{'summary': 'This spot is popular', 'type': '...   
1   [{'summary': 'This spot is popular', 'type': '...   
2   [{'summary': 'This spot is popular', 'type': '...   
3   [{'summary': 'This spot is popular', 'type': '...   
4   [{'summary': 'This spot is popular', 'type': '...   
5   [{'summary': 'This spot is popular', 'type': '...   
6   [{'summary': 'This spot is popular', 'type': '...   
7   [{'summary': 'This spot is popular', 'type': '...   
8   [{'summary': 'This spot is popular', 'type': '...   
9   [{'summary': 'This spot is popular', 'type': '...   
10  [{'summary': 'This spot is popular', 'type': '...   
11  [{'summary': 'This spot is popular', 'type': '...   
12  [{'summary': 'This spot is popular', 'type': '...   
13  [{'summary': 'This spot is popular', 'type': '...   
14  [{'summary': 'This spot is popular', 'type': '...   
15  [{'summary': 'This spot is popular', 'type': '...   
16  [{'summary': 'This spot is 

**Fourth step:** We drop every venue that does not have the right Postal Code for the recent request

In [17]:
df_venue=df_venue[df_venue['venue.location.formattedAddress'].str.contains(df2.loc[j,'Postal Code'])]
df_venue

referralId  reasons.count  \
0    e-0-4b16e8b6f964a52051bf23e3-0              0   
3    e-0-54c3d9ed498e50c810920ee4-3              0   
4    e-0-4b5f1f11f964a52047a729e3-4              0   
5    e-0-55fc4738498ea821b8d881ae-5              0   
7    e-0-5ae3d754d3cce8002c86cbe1-7              0   
8    e-0-4b0ecb01f964a5201b5b23e3-8              0   
10  e-0-4db7044fa86e8d2707b7795e-10              0   
13  e-0-4b9e6ed5f964a52048e336e3-13              0   
14  e-0-4b3a4021f964a520f76225e3-14              0   
15  e-0-507d95038055b398c78eec04-15              0   
16  e-0-4da88e6d5da3ef8bf1613837-16              0   
17  e-0-5a32e7f3f427de60fcef7751-17              0   
19  e-0-4b6f005af964a520f1d52ce3-19              0   
20  e-0-4af79aadf964a520070a22e3-20              0   
21  e-0-5c426e34065ef5002c050b40-21              0   
22  e-0-4bf71abfb182c9b66829755a-22              0   
24  e-0-4be8263a947820a1a283b4db-24              0   
25  e-0-4fa4ae40e4b02443361f27c4-25              0   
26  e-0-4be35c5eb02ec9b64c644fc0-26              0   
30  e-0-5218128011d2f9bf38d27de8-30              0   
31  e-0-4becbb0b0ddaa593c5041ec3-31              0   
32  e-0-4c581533d12a20a1941768bd-32              0   
34  e-0-4fca5aeee4b053b8ae5eba6d-34              0   
35  e-0-4ae8b081f964a5207cb121e3-35              0   
36  e-0-4baf6adff964a52035fe3be3-36              0   
38  e-0-4b06df4af964a520ebf122e3-38              0   
40  e-0-4e24384e22717a5245e621a4-40              0   
41  e-0-4af3820ef964a5203dee21e3-41              0   
42  e-0-4b008142f964a520fc3e22e3-42              0   
43  e-0-4b896e06f964a520803532e3-43              0   
44  e-0-4bb4d8736444b7130fbbf300-44              0   
45  e-0-4ae766baf964a520fcaa21e3-45              0   
48  e-0-4b8951ebf964a520522b32e3-48              0   
49  e-0-4c2a45962219c928ecd5a248-49              0   
50  e-0-530e5a4e498e9d17ab15ae5d-50              0   
52  e-0-59e7ba996bdee6069e7c2ee9-52              0   
54  e-0-4c42343ed691c9b6c3018e0a-54              0   

                                        reasons.items  \
0   [{'summary': 'This spot is popular', 'type': '...   
3   [{'summary': 'This spot is popular', 'type': '...   
4   [{'summary': 'This spot is popular', 'type': '...   
5   [{'summary': 'This spot is popular', 'type': '...   
7   [{'summary': 'This spot is popular', 'type': '...   
8   [{'summary': 'This spot is popular', 'type': '...   
10  [{'summary': 'This spot is popular', 'type': '...   
13  [{'summary': 'This spot is popular', 'type': '...   
14  [{'summary': 'This spot is popular', 'type': '...   
15  [{'summary': 'This spot is popular', 'type': '...   
16  [{'summary': 'This spot is popular', 'type': '...   
17  [{'summary': 'This spot is popular', 'type': '...   
19  [{'summary': 'This spot is popular', 'type': '...   
20  [{'summary': 'This spot is popular', 'type': '...   
21  [{'summary': 'This spot is popular', 'type': '...   
22  [{'summary': 'This spot is popular', 'type': '...   
24  [{'summary': 'This spot is popular', 'type': '...   
25  [{'summary': 'This spot is popular', 'type': '...   
26  [{'summary': 'This spot is popular', 'type': '...   
30  [{'summary': 'This spot is popular', 'type': '...   
31  [{'summary': 'This spot is popular', 'type': '...   
32  [{'summary': 'This spot is popular', 'type': '...   
34  [{'summary': 'This spot is popular', 'type': '...   
35  [{'summary': 'This spot is popular', 'type': '...   
36  [{'summary': 'This spot is popular', 'type': '...   
38  [{'summary': 'This spot is popular', 'type': '...   
40  [{'summary': 'This spot is popular', 'type': '...   
41  [{'summary': 'This spot is popular', 'type': '...   
42  [{'summary': 'This spot is popular', 'type': '...   
43  [{'summary': 'This spot is popular', 'type': '...   
44  [{'summary': 'This spot is popular', 'type': '...   
45  [{'summary': 'This spot is popular', 'type': '...   
48  [{'summary': 'This spot is popular', 'type': '...   
49  [{'summary': 'This spot is pop

Let's put step 2-4 in a loop and use this loop to get the venues for all the neighbourhoods.

In [31]:
df_venues_neigh=pd.DataFrame()#columns=['referralId','reasons.count','reasons.items','venue.id','venue.name','venue.location.address','venue.location.crossStreet','venue.location.lat','venue.location.lng','venue.location.labeledLatLngs','...','venue.location.cc','venue.location.city','venue.location.state','venue.location.country','venue.location.formattedAddress','venue.categories','venue.photos.count','venue.photos.groups','venue.location.neighborhood','venue.venuePage.id'])
for j in range(len(df2)):
    neighborhood_latitude = df2.loc[j, 'Latitude'] # neighborhood latitude value
    neighborhood_longitude = df2.loc[j, 'Longitude'] # neighborhood longitude value
    name=df2.loc[j, 'Neighbourhood']
    radius=800
    LIMIT=100
    nvenues=0
    while nvenues<50:
        url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{}&v={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, neighborhood_latitude, neighborhood_longitude, VERSION, radius, LIMIT)
        results = requests.get(url).json()
        nvenues=len(results['response']['groups'][0]['items'])
        if (nvenues <50):
            radius=radius+500
            print(name+ ': '+str(nvenues) + ' venues found, radius increased to '+str(radius))
        else:
            print(name+ ': '+str(nvenues) + ' venues found')
    items = results['response']['groups'][0]['items']
    df_venue= pd.json_normalize(items)
    df_venue['venue.location.formattedAddress']=df_venue['venue.location.formattedAddress'].apply(', '.join)
    df_venue=df_venue[df_venue['venue.location.formattedAddress'].str.contains(df2.loc[j,'Postal Code'])]
    df_venues_neigh=df_venues_neigh.append(df_venue)
df_venues_neigh

Parkwoods: 5 venues found, radius increased to 1300
Parkwoods: 35 venues found, radius increased to 1800
Parkwoods: 96 venues found
Victoria Village: 9 venues found, radius increased to 1300
Victoria Village: 37 venues found, radius increased to 1800
Victoria Village: 71 venues found
Regent Park, Harbourfront: 82 venues found
Lawrence Manor, Lawrence Heights: 35 venues found, radius increased to 1300
Lawrence Manor, Lawrence Heights: 94 venues found
Queen's Park, Ontario Provincial Government: 100 venues found
Islington Avenue, Humber Valley Village: 10 venues found, radius increased to 1300
Islington Avenue, Humber Valley Village: 22 venues found, radius increased to 1800
Islington Avenue, Humber Valley Village: 41 venues found, radius increased to 2300
Islington Avenue, Humber Valley Village: 55 venues found
Malvern, Rouge: 12 venues found, radius increased to 1300
Malvern, Rouge: 26 venues found, radius increased to 1800
Malvern, Rouge: 32 venues found, radius increased to 2300
Malv

Downsview: 4 venues found, radius increased to 1300
Downsview: 24 venues found, radius increased to 1800
Downsview: 50 venues found
Studio District: 100 venues found
Bedford Park, Lawrence Manor East: 42 venues found, radius increased to 1300
Bedford Park, Lawrence Manor East: 89 venues found
Del Ray, Mount Dennis, Keelsdale and Silverthorn: 11 venues found, radius increased to 1300
Del Ray, Mount Dennis, Keelsdale and Silverthorn: 42 venues found, radius increased to 1800
Del Ray, Mount Dennis, Keelsdale and Silverthorn: 45 venues found, radius increased to 2300
Del Ray, Mount Dennis, Keelsdale and Silverthorn: 100 venues found
Humberlea, Emery: 5 venues found, radius increased to 1300
Humberlea, Emery: 13 venues found, radius increased to 1800
Humberlea, Emery: 41 venues found, radius increased to 2300
Humberlea, Emery: 57 venues found
Birch Cliff, Cliffside West: 7 venues found, radius increased to 1300
Birch Cliff, Cliffside West: 13 venues found, radius increased to 1800
Birch Cli

referralId  reasons.count  \
0    e-0-4b8991cbf964a520814232e3-0              0   
1    e-0-4bd4846a6798ef3bd0c5618d-1              0   
5    e-0-4b8ec91af964a520053733e3-5              0   
6    e-0-57e286f2498e43d84d92d34a-6              0   
15  e-0-58a8dcaa6119f47b9a94dc05-15              0   
..                              ...            ...   
68  e-0-4c4affcfc9e4ef3b5d3fed10-68              0   
72  e-0-4d0408907d9ba35d83856323-72              0   
75  e-0-4b0703f6f964a52080f522e3-75              0   
78  e-0-4be5bc1d2457a593d3eaab15-78              0   
82  e-0-50cf7872e4b08217676abc90-82              0   

                                        reasons.items  \
0   [{'summary': 'This spot is popular', 'type': '...   
1   [{'summary': 'This spot is popular', 'type': '...   
5   [{'summary': 'This spot is popular', 'type': '...   
6   [{'summary': 'This spot is popular', 'type': '...   
15  [{'summary': 'This spot is popular', 'type': '...   
..                                                ...   
68  [{'summary': 'This spot is popular', 'type': '...   
72  [{'summary': 'This spot is popular', 'type': '...   
75  [{'summary': 'This spot is popular', 'type': '...   
78  [{'summary': 'This spot is popular', 'type': '...   
82  [{'summary': 'This spot is popular', 'type': '...   

                    venue.id                   venue.name  \
0   4b8991cbf964a520814232e3              Allwyn's Bakery   
1   4bd4846a6798ef3bd0c5618d  Donalda Golf & Country Club   
5   4b8ec91af964a520053733e3           Graydon Hall Manor   
6   57e286f2498e43d84d92d34a                  Tim Hortons   
15  58a8dcaa6119f47b9a94dc05                          A&W   
..                       ...                          ...   
68  4c4affcfc9e4ef3b5d3fed10                     Goodwill   
72  4d0408907d9ba35d83856323   King's Garden Banquet Hall   
75  4b0703f6f964a52080f522e3               ShaSha Organic   
78  4be5bc1d2457a593d3eaab15                  Fogh Marine   
82  50cf7872e4b08217676abc90            Costco Food Court   

      venue.location.address  venue.location.lat  venue.location.lng  \
0         81 Underhill drive           43.759840          -79.324719   
1             12 Bushbury Dr           43.752816          -79.342741   
5     185 Graydon Hall Drive           43.763923          -79.342961   
6             215 Brookbanks           43.760668          -79.326368   
15      1277 York Mills Road           43.760643          -79.326865   
..                       ...                 ...                 ...   
68        871 Islington Ave.           43.621602          -79.513198   
72        15 Canmotor Avenue           43.622929          -79.510698   
75           20 Plastics Ave           43.623370          -79.509302   
78             901 Oxford St           43.619122          -79.514810   
82  50 Queen Elizabeth Blvd.           43.622727          -79.507455   

                        venue.location.labeledLatLngs  \
0   [{'label': 'display', 'lat': 43.75984035203157...   
1   [{'label': 'display', 'lat': 43.75281596740471...   
5   [{'label': 'display', 'lat': 43.76392256055678...   
6   [{'label': 'display', 'lat': 43.76066827030228...   
15  [{'label': 'display', 'lat': 43.76064307616131...   
..                                                ...   
68  [{'label': 'display', 'lat': 43.62160166310763...   
72  [{'label': 'display', 'lat': 43.6229291, 'lng'...   
75  [{'label': 'display', 'lat': 43.62337, 'lng': ...   
78  [{'label': 'display', 'lat': 43.61912207338791...   
82  [{'label': 'display', 'lat': 43.62272689757317...   

    venue.location.distance  ... venue.location.state venue.location.country  \
0                       833  ...                   ON                 Canada   
1                      1053  ...                   ON                 Canada   
5                      1597  ...                   ON                 Canada   
6                       866  ...                   ON                 Canada   
15      

We used a large amount of the 950 requests we can send, so let's copy the data we obtained in an other Dataframe we will work with and save the obtained data into a csv so we don't have to get it again.

In [35]:
df_venues2=df_venues_neigh.reset_index()
df_venues2.to_csv('Venues.csv')

We would like to display all of the venues on the map with the marker-cluster-plugin of folium.

In [38]:
import folium.plugins as fplugins
lat=43.66135
long=-79.383087

map_toronto2 = folium.Map(location=[lat, long], zoom_start=10,control_scale = True)

# instantiate a mark cluster object
venues_cluster = fplugins.MarkerCluster().add_to(map_toronto2)

# loop through the dataframe and add each data point to the mark cluster
for lat, lng, label, in zip(df_venues2['venue.location.lat'], df_venues2['venue.location.lng'],df_venues2['venue.name']):
    folium.Marker(
        location=[lat, lng],
        icon=None,
        popup=label,
    ).add_to(venues_cluster)

# display map
map_toronto2

As we can see, the largest ammount of venues seem to be found in downtown. Let's use a more scientific version to cluster the spatial data of the locations. We will use the density-based clustering algorithm DBSCAN from the sklearn library.

In [99]:
from sklearn.cluster import DBSCAN

ClusterData = df_venues2[['venue.location.lat','venue.location.lng']]
db = DBSCAN(eps=0.005, min_samples=20).fit(ClusterData)
labels = db.labels_
unique_labels = set(labels)
print(unique_labels)
df_venues2['cluster_label']=labels
df_venues2

{0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, -1}


index                       referralId  reasons.count  \
0         0   e-0-4b8991cbf964a520814232e3-0              0   
1         1   e-0-4bd4846a6798ef3bd0c5618d-1              0   
2         5   e-0-4b8ec91af964a520053733e3-5              0   
3         6   e-0-57e286f2498e43d84d92d34a-6              0   
4        15  e-0-58a8dcaa6119f47b9a94dc05-15              0   
...     ...                              ...            ...   
3050     68  e-0-4c4affcfc9e4ef3b5d3fed10-68              0   
3051     72  e-0-4d0408907d9ba35d83856323-72              0   
3052     75  e-0-4b0703f6f964a52080f522e3-75              0   
3053     78  e-0-4be5bc1d2457a593d3eaab15-78              0   
3054     82  e-0-50cf7872e4b08217676abc90-82              0   

                                          reasons.items  \
0     [{'summary': 'This spot is popular', 'type': '...   
1     [{'summary': 'This spot is popular', 'type': '...   
2     [{'summary': 'This spot is popular', 'type': '...   
3     [{'summary': 'This spot is popular', 'type': '...   
4     [{'summary': 'This spot is popular', 'type': '...   
...                                                 ...   
3050  [{'summary': 'This spot is popular', 'type': '...   
3051  [{'summary': 'This spot is popular', 'type': '...   
3052  [{'summary': 'This spot is popular', 'type': '...   
3053  [{'summary': 'This spot is popular', 'type': '...   
3054  [{'summary': 'This spot is popular', 'type': '...   

                      venue.id                   venue.name  \
0     4b8991cbf964a520814232e3              Allwyn's Bakery   
1     4bd4846a6798ef3bd0c5618d  Donalda Golf & Country Club   
2     4b8ec91af964a520053733e3           Graydon Hall Manor   
3     57e286f2498e43d84d92d34a                  Tim Hortons   
4     58a8dcaa6119f47b9a94dc05                          A&W   
...                        ...                          ...   
3050  4c4affcfc9e4ef3b5d3fed10                     Goodwill   
3051  4d0408907d9ba35d83856323   King's Garden Banquet Hall   
3052  4b0703f6f964a52080f522e3               ShaSha Organic   
3053  4be5bc1d2457a593d3eaab15                  Fogh Marine   
3054  50cf7872e4b08217676abc90            Costco Food Court   

        venue.location.address  venue.location.lat  venue.location.lng  \
0           81 Underhill drive           43.759840          -79.324719   
1               12 Bushbury Dr           43.752816          -79.342741   
2       185 Graydon Hall Drive           43.763923          -79.342961   
3               215 Brookbanks           43.760668          -79.326368   
4         1277 York Mills Road           43.760643          -79.326865   
...                        ...                 ...                 ...   
3050        871 Islington Ave.           43.621602          -79.513198   
3051        15 Canmotor Avenue           43.622929          -79.510698   
3052           20 Plastics Ave           43.623370          -79.509302   
3053             901 Oxford St           43.619122          -79.514810   
3054  50 Queen Elizabeth Blvd.           43.622727          -79.507455   

                          venue.location.labeledLatLngs  ...  \
0     [{'label': 'display', 'lat': 43.75984035203157...  ...   
1     [{'label': 'display', 'lat': 43.75281596740471...  ...   
2     [{'label': 'display', 'lat': 43.76392256055678...  ...   
3     [{'label': 'display', 'lat': 43.76066827030228...  ...   
4     [{'label': 'display', 'lat': 43.76064307616131...  ...   
...                                                 ...  ...   
3050  [{'label': 'display', 'lat': 43.62160166310763...  ...   
3051  [{'label': 'display', 'lat': 43.6229291, 'lng'...  ...   
3052  [{'label': 'display', 'lat': 43.62337, 'lng': ...  ...   
3053  [{'label': 'display', 'lat': 43.61912207338791...  ...   
3054  [{'label': 'display', 'lat': 43.62272689757317...  ...   

      venue.location.country  \
0                     Canada   
1                     Canada   
2                     Canada 

Let's have a look at our spatial venue clusters.

In [104]:
palette = ['blue', 'cadetblue', 'darkblue', 'darkgreen', 'darkpurple', 'darkred', 'gray', 'green', 'lightblue', 'lightgray', 'lightgreen', 'lightred', 'orange', 'pink', 'purple', 'red', 'white','beige','black','blue', 'cadetblue', 'darkblue', 'darkgreen', 'darkpurple', 'darkred', 'gray', 'green', 'lightblue', 'lightgray', 'lightgreen', 'lightred', 'orange', 'pink', 'purple', 'red', 'white','beige','black','blue', 'cadetblue', 'darkblue', 'darkgreen', 'darkpurple', 'darkred', 'gray', 'green', 'lightblue', 'lightgray', 'lightgreen', 'lightred', 'orange', 'pink', 'purple', 'red', 'white','beige','black']

map_toronto3 = folium.Map(location=[lat, long], zoom_start=11,control_scale = True)
for i in range(0,len(unique_labels)-1):
    df_venues3=df_venues2[df_venues2['cluster_label']==i]
    for lat, lng, name, in zip(df_venues3['venue.location.lat'], df_venues3['venue.location.lng'],df_venues3['venue.name']):
        label = folium.Popup(name, parse_html=True)
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup=name,
            color=palette[i],
            fill=True,
            fill_color=palette[i],
            fill_opacity=1,
            parse_html=False).add_to(map_toronto3)

map_toronto3


As we expected, the largest venue cluster is in Downtown Toronto. Other clusters include main streets, e.g. Avenue Road (white markers) and St.Clair Avenue West (grey markers); Malls, e.g. Bayview Village (orange markers) and Yorkdale Shopping Centre (cadetblue markers); and central places in the suburbs, e.g. the North York Centre (black markers).